In [1]:
%matplotlib inline
import numpy as np
import pandas as pd
import scipy
import sklearn
import spacy
import matplotlib.pyplot as plt
import seaborn as sns
import re
from nltk.corpus import gutenberg, stopwords
from collections import Counter

from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression

from sklearn import ensemble

from sklearn.svm import SVC

from sklearn import datasets, linear_model
from sklearn.model_selection import cross_val_score

import nltk
from nltk.tokenize import word_tokenize

In [2]:
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/vincentgomez/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


True

In [3]:
# Utility function for standard text cleaning.
def text_cleaner(text):
    # Visual inspection identifies a form of punctuation spaCy does not
    # recognize: the double dash '--'.  Better get rid of it now!
    text = re.sub(r'--',' ',text)
    text = re.sub("[\[].*?[\]]", "", text)
    text = ' '.join(text.split())
    return text
    
# Load and clean the data.
persuasion = gutenberg.raw('austen-persuasion.txt')
alice = gutenberg.raw('carroll-alice.txt')

# The Chapter indicator is idiosyncratic
persuasion = re.sub(r'Chapter \d+', '', persuasion)
alice = re.sub(r'CHAPTER .*', '', alice)
    
alice = text_cleaner(alice)
persuasion = text_cleaner(persuasion)

In [4]:
# Parse the cleaned novels. This can take a bit.
nlp = spacy.load('en')
alice_doc = nlp(alice)
persuasion_doc = nlp(persuasion)

In [5]:
# Group into sentences.
alice_sents = [[sent, "Carroll"] for sent in alice_doc.sents]
persuasion_sents = [[sent, "Austen"] for sent in persuasion_doc.sents]
# Combine the sentences from the two novels into one data frame.
sentences = pd.DataFrame(alice_sents + persuasion_sents)
sentences.head()

0        1
0  (Alice, was, beginning, to, get, very, tired, ...  Carroll
1  (So, she, was, considering, in, her, own, mind...  Carroll
2  (There, was, nothing, so, VERY, remarkable, in...  Carroll
3                                      (Oh, dear, !)  Carroll
4                         (I, shall, be, late, !, ')  Carroll

In [150]:
# Utility function to create a list of the 2000 most common words.
def bag_of_words(text):
    
    # Filter out punctuation and stop words.
    allwords = [token.lemma_
                for token in text
                if not token.is_punct
                and not token.is_stop]
    
    # Return the most common words.
    return [item[0] for item in Counter(allwords).most_common(2000)]
    
# Set up the bags.
alicewords = bag_of_words(alice_doc)
persuasionwords = bag_of_words(persuasion_doc)

# Combine bags to create a set of unique words.
common_words = set(alicewords + persuasionwords)

In [7]:
hello = [token.lemma_
         for token in alice_doc
         if not token.is_punct
         and not token.is_stop]

In [8]:
Counter(hello)

Counter({'bite': 3,
         'keep': 17,
         'nobody': 3,
         'vegetable': 1,
         'curtseying': 1,
         'earnestly': 2,
         'toffee': 1,
         'silence': 14,
         'fountain': 2,
         'sand': 2,
         'owl': 3,
         'saucer': 1,
         'cook': 13,
         'cheshire': 7,
         'drawling': 2,
         'age': 4,
         'spirited': 1,
         'twentieth': 1,
         'caper': 1,
         'swallow': 3,
         'bat': 7,
         'australia': 1,
         'roast': 1,
         'egg': 6,
         'care': 6,
         'person': 5,
         'root': 2,
         'timidly': 9,
         'less': 1,
         'immediate': 1,
         'royal': 2,
         'if': 18,
         'good': 43,
         'have': 62,
         'anxious': 3,
         'date': 1,
         'brother': 1,
         'know': 107,
         'down': 2,
         'conquest': 1,
         'ugly': 2,
         'thick': 1,
         'creep': 2,
         'capital': 4,
         'short': 6,
         'impos

In [166]:
# Creates a data frame with features for each word in our common word set.
# Each value is the count of the times the word appears in each sentence.
def bow_features(sentences, common_words):
    
    # Scaffold the data frame and initialize counts to zero.
    df = pd.DataFrame(columns=common_words)
    df['text_sentence'] = sentences[0]
    df['text_source'] = sentences[1]
    df.loc[:, common_words] = 0
    
    # Process each row, counting the occurrence of words in each sentence.
    for i, sentence in enumerate(df['text_sentence']):
        
        # Convert the sentence to lemmas, then filter out punctuation,
        # stop words, and uncommon words.
        words = [token.lemma_
                 for token in sentence
                 if (
                     not token.is_punct
                     and not token.is_stop
                     and token.lemma_ in common_words
                 )]
        
        # Populate the row with word counts.
        for word in words:
            df.loc[i, word] += 1
        
        # This counter is just to make sure the kernel didn't hang.
        if i % 500 == 0:
            print("Processing row {}".format(i))
            
    return df

# Create our data frame with features. This can take a while to run.
word_counts = bow_features(sentences, common_words)
word_counts.head()

Processing row 0
Processing row 500
Processing row 1000
Processing row 1500
Processing row 2000
Processing row 2500
Processing row 3000
Processing row 3500
Processing row 4000
Processing row 4500
Processing row 5000


keep behaviour style bustle vision degrading earnestly fortune toffee  \
0    0         0     0      0      0         0         0       0      0   
1    0         0     0      0      0         0         0       0      0   
2    0         0     0      0      0         0         0       0      0   
3    0         0     0      0      0         0         0       0      0   
4    0         0     0      0      0         0         0       0      0   

  calculate dowager previous revert composedly saucer cook smiths twelve  \
0         0       0        0      0          0      0    0      0      0   
1         0       0        0      0          0      0    0      0      0   
2         0       0        0      0          0      0    0      0      0   
3         0       0        0      0          0      0    0      0      0   
4         0       0        0      0          0      0    0      0      0   

  caper principal egg care scarcely person timidly fresh remarkably less  \
0     0         0   0    0        0      0       0     0          0    0   
1     0         0   0    0        0      0       0     0          0    0   
2     0         0   0    0        0      0       0     0          0    0   
3     0         0   0    0        0      0       0     0          0    0   
4     0         0   0    0        0      0       0     0          0    0   

  publication tolerable monday counsel powerful good have ship nest down  \
0           0         0      0       0        0    0    1    0    0    0   
1           0         0      0       0        0    0    0    0    0    0   
2           0         0      0       0        0    0    0    0    0    0   
3           0         0      0       0        0    0    0    0    0    0   
4           0         0      0       0        0    0    0    0    0    0   

  conquest caution charles offence connexion busy condition free destroy  \
0        0       0       0       0         0    0         0    0       0   
1        0       0       0       0         0    0         0    0       0   
2        0       0       0       0         0    0         0    0       0   
3        0       0       0       0         0    0         0    0       0   
4        0       0       0       0         0    0         0    0       0   

  aside lower uncommon pennyworth bottle death hopeless art understand  \
0     0     0        0          0      0     0        0   0          0   
1     0     0        0          0      0     0        0   0          0   
2     0     0        0          0      0     0        0   0          0   
3     0     0        0          0      0     0        0   0          0   
4     0     0        0          0      0     0        0   0          0   

  purchase till tenderness severity courteous pour cherry fair joy john alarm  \
0        0    0          0        0         0    0      0    0   0    0     0   
1        0    0          0        0         0    0      0    0   0    0     0   
2        0    0          0        0         0    0      0    0   0    0     0   
3        0    0          0        0         0    0      0    0   0    0     0   
4        0    0          0        0         0    0      0    0   0    0     0   

  comfortable alarming howl lay private marlborough station acknowledge dinn  \
0           0        0    0   0       0           0       0           0    0   
1           0        0    0   0       0           0       0           0    0   
2           0        0    0   0       0           0       0           0    0   
3           0        0    0   0       0           0       0           0    0   
4           0        0    0   0       0           0       0           0    0   

  sulkily rule rudeness sight reflect tease scale ten mabel artificial  \
0       0    0        0     0       0     0     0   0     0          0   
1       0    0        0     0       0     0     0   0     0          0   
2       0    0        0     0       0     0     0   0     0          0   
3       0    0

In [115]:
word_counts.shape

(5318, 3065)

In [106]:
len(common_words)

3063

### I don't know why, but for some reason my scores are slightly lower than what's in the curriculum and I cut and pasted the whole thing! I did change the test size from 0.4 to 0.2 though and that brought it closer. And from what I can see, the X_train, y_train shapes are different.

In [11]:
rfc = ensemble.RandomForestClassifier()
Y = word_counts['text_source']
X = np.array(word_counts.drop(['text_sentence','text_source'], 1))

X_train, X_test, y_train, y_test = train_test_split(X, 
                                                    Y,
                                                    test_size=0.2,
                                                    random_state=0)
train = rfc.fit(X_train, y_train)

print('Training set score:', rfc.score(X_train, y_train))
print('\nTest set score:', rfc.score(X_test, y_test))

Training set score: 0.988011283498

Test set score: 0.906015037594


In [167]:
Y = word_counts['text_source']
X = np.array(word_counts.drop(['text_sentence','text_source'], 1))

X_train, X_test, y_train, y_test = train_test_split(X, 
                                                    Y,
                                                    test_size=0.2,
                                                    random_state=0)

lr = LogisticRegression()
train = lr.fit(X_train, y_train)
print(X_train.shape, y_train.shape)

log_reg_train_score1 = lr.score(X_train, y_train)
log_reg_test_score1 = lr.score(X_test, y_test)
print('Training set score:', log_reg_train_score1)
print('\nTest set score:', log_reg_test_score1)

(4254, 3063) (4254,)
Training set score: 0.956511518571

Test set score: 0.926691729323


In [13]:
clf = ensemble.GradientBoostingClassifier()
train = clf.fit(X_train, y_train)

print('Training set score:', clf.score(X_train, y_train))
print('\nTest set score:', clf.score(X_test, y_test))

Training set score: 0.882463563705

Test set score: 0.862781954887


### Now with Emma! This one too, despite basically copying and pasting the work, also has a much lower score from 70% to 65% accuracy... :-/

### I'm going to comment out the Emma stuff because it takes WAY TOO LONG to process and I don't want to have to wait through it each time I run this notebook...

In [14]:
# # Clean the Emma data.
# emma = gutenberg.raw('austen-emma.txt')
# emma = re.sub(r'VOLUME \w+', '', emma)
# emma = re.sub(r'CHAPTER \w+', '', emma)
# emma = text_cleaner(emma)
# print(emma[:100])

In [15]:
# # Parse our cleaned data.
# emma_doc = nlp(emma)

In [16]:
# # Group into sentences.
# persuasion_sents = [[sent, "Austen"] for sent in persuasion_doc.sents]
# emma_sents = [[sent, "Austen"] for sent in emma_doc.sents]

# # Emma is quite long, let's cut it down to the same length as Alice.
# emma_sents = emma_sents[0:len(alice_sents)]

In [17]:
# # Build a new Bag of Words data frame for Emma word counts.
# # We'll use the same common words from Alice and Persuasion.
# emma_sentences = pd.DataFrame(emma_sents)
# emma_bow = bow_features(emma_sentences, common_words)

# print('done')

In [18]:
# emma_sentences.head()

In [19]:
# # Now we can model it!
# # Let's use logistic regression again.

# # Combine the Emma sentence data with the Alice data from the test set.
# X_Emma_test = np.concatenate((
#     X_train[y_train[y_train=='Carroll'].index],
#     emma_bow.drop(['text_sentence','text_source'], 1)
# ), axis=0)
# y_Emma_test = pd.concat([y_train[y_train=='Carroll'],
#                          pd.Series(['Austen'] * emma_bow.shape[0])])

# # Model.
# print('\nTest set score:', lr.score(X_Emma_test, y_Emma_test))
# lr_Emma_predicted = lr.predict(X_Emma_test)
# pd.crosstab(y_Emma_test, lr_Emma_predicted)

### First, I'm going to try the support vector machine for classification... It worked about as well as the logistic regression model.

In [168]:
Y = word_counts['text_source']
X = np.array(word_counts.drop(['text_sentence','text_source'], 1))

X_train, X_test, y_train, y_test = train_test_split(X, 
                                                    Y,
                                                    test_size=0.2,
                                                    random_state=0)

svm = SVC(kernel = 'linear')
svm.fit(X_train, y_train)

SVC(C=1.0, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma='auto', kernel='linear',
  max_iter=-1, probability=False, random_state=None, shrinking=True,
  tol=0.001, verbose=False)

In [169]:
svm_train_score1 = svm.score(X_train, y_train)
svm_test_score1 = svm.score(X_test, y_test)

print('Training set score:', svm_train_score1)
print('\nTest set score:', svm_test_score1)

Training set score: 0.967795016455

Test set score: 0.913533834586


### Now I'm going to add two features to see if that changes anything: Sentence length and the number of unique words per sentence.

In [154]:
word_counts.shape

(5318, 3065)

In [26]:
example_sentence = word_counts.iloc[0,word_counts.shape[1]-2]
example_sentence

Alice was beginning to get very tired of sitting by her sister on the bank, and of having nothing to do: once or twice she had peeped into the book her sister was reading, but it had no pictures or conversations in it, 'and what is the use of a book,' thought Alice 'without pictures or conversation?'

In [27]:
# Look at some metrics around this sentence.
example_words = [token for token in example_sentence if not token.is_punct]
unique_words = set([token.text for token in example_words])

In [28]:
len(example_words)

57

In [29]:
len(unique_words)

41

In [116]:
sentence_lengths = []
unique_words_length = []
for i in range(word_counts.shape[0]):
    example_sentence = word_counts.iloc[i,word_counts.shape[1]-2]
    example_words = [token for token in example_sentence if not token.is_punct]
    length = len(example_words)
    sentence_lengths.append(length)
    unique_length = len(set([token.text for token in example_words]))
    unique_words_length.append(unique_length)

In [155]:
word_sent_counts = word_counts

In [118]:
len(sentence_lengths)

5318

In [119]:
len(unique_words_length)

5318

In [156]:
word_sent_counts['sentence_lengths'] = sentence_lengths
word_sent_counts['unique_words_length'] = unique_words_length

In [157]:
word_sent_counts.head()

keep behaviour style bustle vision degrading earnestly fortune toffee  \
0    0         0     0      0      0         0         0       0      0   
1    0         0     0      0      0         0         0       0      0   
2    0         0     0      0      0         0         0       0      0   
3    0         0     0      0      0         0         0       0      0   
4    0         0     0      0      0         0         0       0      0   

  calculate dowager previous revert composedly saucer cook smiths twelve  \
0         0       0        0      0          0      0    0      0      0   
1         0       0        0      0          0      0    0      0      0   
2         0       0        0      0          0      0    0      0      0   
3         0       0        0      0          0      0    0      0      0   
4         0       0        0      0          0      0    0      0      0   

  caper principal egg care scarcely person timidly fresh remarkably less  \
0     0         0   0    0        0      0       0     0          0    0   
1     0         0   0    0        0      0       0     0          0    0   
2     0         0   0    0        0      0       0     0          0    0   
3     0         0   0    0        0      0       0     0          0    0   
4     0         0   0    0        0      0       0     0          0    0   

  publication tolerable monday counsel powerful good have ship nest down  \
0           0         0      0       0        0    0    1    0    0    0   
1           0         0      0       0        0    0    0    0    0    0   
2           0         0      0       0        0    0    0    0    0    0   
3           0         0      0       0        0    0    0    0    0    0   
4           0         0      0       0        0    0    0    0    0    0   

  conquest caution charles offence connexion busy condition free destroy  \
0        0       0       0       0         0    0         0    0       0   
1        0       0       0       0         0    0         0    0       0   
2        0       0       0       0         0    0         0    0       0   
3        0       0       0       0         0    0         0    0       0   
4        0       0       0       0         0    0         0    0       0   

  aside lower uncommon pennyworth bottle death hopeless art understand  \
0     0     0        0          0      0     0        0   0          0   
1     0     0        0          0      0     0        0   0          0   
2     0     0        0          0      0     0        0   0          0   
3     0     0        0          0      0     0        0   0          0   
4     0     0        0          0      0     0        0   0          0   

  purchase till tenderness severity courteous pour cherry fair joy john alarm  \
0        0    0          0        0         0    0      0    0   0    0     0   
1        0    0          0        0         0    0      0    0   0    0     0   
2        0    0          0        0         0    0      0    0   0    0     0   
3        0    0          0        0         0    0      0    0   0    0     0   
4        0    0          0        0         0    0      0    0   0    0     0   

  comfortable alarming howl lay private marlborough station acknowledge dinn  \
0           0        0    0   0       0           0       0           0    0   
1           0        0    0   0       0           0       0           0    0   
2           0        0    0   0       0           0       0           0    0   
3           0        0    0   0       0           0       0           0    0   
4           0        0    0   0       0           0       0           0    0   

  sulkily rule rudeness sight reflect tease scale ten mabel artificial  \
0       0    0        0     0       0     0     0   0     0          0   
1       0    0        0     0       0     0     0   0     0          0   
2       0    0        0     0       0     0     0   0     0          0   
3       0    0

### So, I added my two new features. Now going to try it with logistic regression. It was slightly better with a jump from 0.957 to 0.963 in the training test and a jump from 0.916 to 0.917 in the test set.

In [158]:
Y = word_sent_counts['text_source']
X = np.array(word_sent_counts.drop(['text_sentence','text_source'], 1))

X_train, X_test, y_train, y_test = train_test_split(X, 
                                                    Y,
                                                    test_size=0.2,
                                                    random_state=0)

lr2 = LogisticRegression()
train = lr2.fit(X_train, y_train)
print(X_train.shape, y_train.shape)

log_reg_train_score2 = lr2.score(X_train, y_train)
log_reg_text_score2 = lr2.score(X_test, y_test)

print('Training set score with sentence features:', log_reg_train_score2)
print('\nTest set score with sentence features:', log_reg_text_score2)

print('\nOriginal Log Regression Train Score: ', log_reg_train_score1)
print('\nOriginal Log Regression Test Score: ', log_reg_test_score1)

(4254, 3065) (4254,)
Training set score with sentence features: 0.960272684532

Test set score with sentence features: 0.923872180451

Original Log Regression Train Score:  0.956511518571

Original Log Regression Test Score:  0.926691729323


### The SVM actually broke 97% on using the sentence features

In [173]:
Y = word_sent_counts['text_source']
X = np.array(word_sent_counts.drop(['text_sentence','text_source'], 1))

X_train, X_test, y_train, y_test = train_test_split(X, 
                                                    Y,
                                                    test_size=0.2,
                                                    random_state=0)



svm2 = SVC(kernel = 'linear')
svm2.fit(X_train, y_train)

svm_train_score2 = svm2.score(X_train, y_train)
svm_test_score2 = svm2.score(X_test, y_test)

print('Training set score with sentance features:', svm_train_score2)
print('\nTest set score with sentance features:', svm_test_score2)

print('\nTraining set score original features:', svm_train_score1)
print('\nTest set score original features:', svm_test_score1)

Training set score with sentance features: 0.974847202633

Test set score with sentance features: 0.925751879699

Training set score original features: 0.967795016455

Test set score original features: 0.913533834586


### Now let's try parts of speech!!!

In [45]:
example_sentence = word_counts.loc[0,'text_sentence']
example_sentence

Alice was beginning to get very tired of sitting by her sister on the bank, and of having nothing to do: once or twice she had peeped into the book her sister was reading, but it had no pictures or conversations in it, 'and what is the use of a book,' thought Alice 'without pictures or conversation?'

In [46]:
# View the part of speech for some tokens in our sentence.
parts_of_speech = []
for token in example_sentence:
    parts_of_speech.append(token.pos_)

In [47]:
len(set(parts_of_speech))

11

In [48]:
parts_of_speech

['PROPN',
 'VERB',
 'VERB',
 'PART',
 'VERB',
 'ADV',
 'ADJ',
 'ADP',
 'VERB',
 'ADP',
 'ADJ',
 'NOUN',
 'ADP',
 'DET',
 'NOUN',
 'PUNCT',
 'CCONJ',
 'ADP',
 'VERB',
 'NOUN',
 'PART',
 'VERB',
 'PUNCT',
 'ADV',
 'CCONJ',
 'ADV',
 'PRON',
 'VERB',
 'VERB',
 'ADP',
 'DET',
 'NOUN',
 'ADJ',
 'NOUN',
 'VERB',
 'VERB',
 'PUNCT',
 'CCONJ',
 'PRON',
 'VERB',
 'DET',
 'NOUN',
 'CCONJ',
 'NOUN',
 'ADP',
 'PRON',
 'PUNCT',
 'PUNCT',
 'CCONJ',
 'NOUN',
 'VERB',
 'DET',
 'NOUN',
 'ADP',
 'DET',
 'NOUN',
 'PUNCT',
 'PUNCT',
 'VERB',
 'PROPN',
 'PUNCT',
 'ADP',
 'NOUN',
 'CCONJ',
 'NOUN',
 'PUNCT',
 'PUNCT']

In [49]:
from collections import Counter

print(Counter(parts_of_speech).keys()) # equals to list(set(words))
print(Counter(parts_of_speech).values()) # counts the elements' frequency

dict_keys(['PUNCT', 'PROPN', 'ADP', 'ADV', 'PRON', 'CCONJ', 'PART', 'VERB', 'NOUN', 'DET', 'ADJ'])
dict_values([10, 2, 8, 3, 3, 6, 2, 13, 12, 5, 3])


In [50]:
keys = list(Counter(parts_of_speech).keys())
values = list(Counter(parts_of_speech).values())
for i in range(len(Counter(parts_of_speech).keys())):
    print('{}={}'.format(keys[i],values[i]))

PUNCT=10
PROPN=2
ADP=8
ADV=3
PRON=3
CCONJ=6
PART=2
VERB=13
NOUN=12
DET=5
ADJ=3


### My initial idea was to take each parts of speech and add them as features and put the number of occurances for each part of speech into each sentence. Got a little stuck wondering how to do that though. Below is my initial attempt, but I'm not sure if it would work or if I was even on the right track. I did try a google search for POS and "bag of words" but it was pretty useless... lol... Any thoughts?

In [51]:
# for i in range(word_counts.shape[0]):
#     example_sentence = word_counts.iloc[i,3059]
#     parts_of_speech = []
#     for token in example_sentence:
#         parts_of_speech.append(token.pos_)
#     keys = list(Counter(parts_of_speech).keys())
#     values = list(Counter(parts_of_speech).values())
#     for j in len(keys):
#         word_counts.at[i, keys]

In [52]:
# import nltk
# nltk.download('punkt')
# from nltk import pos_tag, word_tokenize
# tokens = nltk.word_tokenize(example_sentence)


In [53]:
example_sentence

Alice was beginning to get very tired of sitting by her sister on the bank, and of having nothing to do: once or twice she had peeped into the book her sister was reading, but it had no pictures or conversations in it, 'and what is the use of a book,' thought Alice 'without pictures or conversation?'

In [54]:
type(example_sentence)

spacy.tokens.span.Span

### Now for a different book... :-P

In [55]:
# Clean the Emma data.
blake = gutenberg.raw('blake-poems.txt')
# blake = re.sub(r'VOLUME \w+', '', emma)
# blake = re.sub(r'CHAPTER \w+', '', emma)
# blake = text_cleaner(emma)
print(blake[:1000])

[Poems by William Blake 1789]

 
SONGS OF INNOCENCE AND OF EXPERIENCE
and THE BOOK of THEL


 SONGS OF INNOCENCE
 
 
 INTRODUCTION
 
 Piping down the valleys wild,
   Piping songs of pleasant glee,
 On a cloud I saw a child,
   And he laughing said to me:
 
 "Pipe a song about a Lamb!"
   So I piped with merry cheer.
 "Piper, pipe that song again;"
   So I piped: he wept to hear.
 
 "Drop thy pipe, thy happy pipe;
   Sing thy songs of happy cheer:!"
 So I sang the same again,
   While he wept with joy to hear.
 
 "Piper, sit thee down and write
   In a book, that all may read."
 So he vanish'd from my sight;
   And I pluck'd a hollow reed,
 
 And I made a rural pen,
   And I stain'd the water clear,
 And I wrote my happy songs
   Every child may joy to hear.
 
 
 THE SHEPHERD
 
 How sweet is the Shepherd's sweet lot!
 From the morn to the evening he stays;
 He shall follow his sheep all the day,
 And his tongue shall be filled with praise.
 
 For he hears the lambs' innocent call,
 And

In [56]:
# Remove the []
pattern = "[\[].*?[\]]"
blake = re.sub(pattern, '', blake)

In [57]:
# Remove the title of each poem

pattern = "[A-Z][A-Z]+"
blake = re.sub(pattern, '', blake)

In [58]:
# Taking out some of the extra lower case words in the title

blake = blake[20:]

In [59]:
blake = ' '.join(blake.split())

In [60]:
blake[:1000]

'Piping down the valleys wild, Piping songs of pleasant glee, On a cloud I saw a child, And he laughing said to me: "Pipe a song about a Lamb!" So I piped with merry cheer. "Piper, pipe that song again;" So I piped: he wept to hear. "Drop thy pipe, thy happy pipe; Sing thy songs of happy cheer:!" So I sang the same again, While he wept with joy to hear. "Piper, sit thee down and write In a book, that all may read." So he vanish\'d from my sight; And I pluck\'d a hollow reed, And I made a rural pen, And I stain\'d the water clear, And I wrote my happy songs Every child may joy to hear. How sweet is the Shepherd\'s sweet lot! From the morn to the evening he stays; He shall follow his sheep all the day, And his tongue shall be filled with praise. For he hears the lambs\' innocent call, And he hears the ewes\' tender reply; He is watching while they are in peace, For they know when their Shepherd is nigh. The sun does arise, And make happy the skies; The merry bells ring To welcome the Spr

In [61]:
blake_doc = nlp(blake)

In [62]:
blake_sents = [[sent, "Blake"] for sent in blake_doc.sents]

In [63]:
blakewords = bag_of_words(blake_doc)

### I will compare blake to alice in wonderland

In [64]:
common_words2 = set(alicewords + blakewords)

In [65]:
blake_sentences = pd.DataFrame(blake_sents)

In [66]:
sentences2 = pd.DataFrame(alice_sents + blake_sents)
sentences2.head()

0        1
0  (Alice, was, beginning, to, get, very, tired, ...  Carroll
1  (So, she, was, considering, in, her, own, mind...  Carroll
2  (There, was, nothing, so, VERY, remarkable, in...  Carroll
3                                      (Oh, dear, !)  Carroll
4                         (I, shall, be, late, !, ')  Carroll

In [67]:
word_counts2 = bow_features(sentences2, common_words2)
word_counts2.head()

Processing row 0
Processing row 500
Processing row 1000
Processing row 1500
Processing row 2000


keep mne vision earnestly whirlpool toffee saucer cook robin caper  \
0    0   0      0         0         0      0      0    0     0     0   
1    0   0      0         0         0      0      0    0     0     0   
2    0   0      0         0         0      0      0    0     0     0   
3    0   0      0         0         0      0      0    0     0     0   
4    0   0      0         0         0      0      0    0     0     0   

      ...     nearly methought engrave steam past overcome milk lock  \
0     ...          0         0       0     0    0        0    0    0   
1     ...          0         0       0     0    0        0    0    0   
2     ...          0         0       0     0    0        0    0    0   
3     ...          0         0       0     0    0        0    0    0   
4     ...          0         0       0     0    0        0    0    0   

                                       text_sentence text_source  
0  (Alice, was, beginning, to, get, very, tired, ...     Carroll  
1  (So, she, was, considering, in, her, own, mind...     Carroll  
2  (There, was, nothing, so, VERY, remarkable, in...     Carroll  
3                                      (Oh, dear, !)     Carroll  
4                         (I, shall, be, late, !, ')     Carroll  

[5 rows x 2563 columns]

### The logistic regression worked really well with blake vs alice... 

In [68]:
Y = word_counts2['text_source']
X = np.array(word_counts2.drop(['text_sentence','text_source'], 1))

X_train, X_test, y_train, y_test = train_test_split(X, 
                                                    Y,
                                                    test_size=0.2,
                                                    random_state=0)

lr3 = LogisticRegression()
train = lr3.fit(X_train, y_train)
print(X_train.shape, y_train.shape)
print('Training set score:', lr3.score(X_train, y_train))
print('\nTest set score:', lr3.score(X_test, y_test))

(1707, 2561) (1707,)
Training set score: 0.976567076743

Test set score: 0.946135831382


### With the sentence lengths, I was able to improve the scores slightly... 

In [69]:
sentence_lengths = []
unique_words_length = []
for i in range(word_counts2.shape[0]):
    example_sentence = word_counts2.iloc[i,(word_counts2.shape[1]-2)]
    example_words = [token for token in example_sentence if not token.is_punct]
    length = len(example_words)
    sentence_lengths.append(length)
    unique_length = len(set([token.text for token in example_words]))
    unique_words_length.append(unique_length)

In [70]:
word_counts2['sentence_lengths'] = sentence_lengths
word_counts2['unique_words_length'] = unique_words_length

In [71]:
Y = word_counts2['text_source']
X = np.array(word_counts2.drop(['text_sentence','text_source'], 1))

X_train, X_test, y_train, y_test = train_test_split(X, 
                                                    Y,
                                                    test_size=0.2,
                                                    random_state=0)

lr3 = LogisticRegression()
train = lr3.fit(X_train, y_train)
print(X_train.shape, y_train.shape)
print('Training set score:', lr3.score(X_train, y_train))
print('\nTest set score:', lr3.score(X_test, y_test))

(1707, 2563) (1707,)
Training set score: 0.977152899824

Test set score: 0.955503512881


In [72]:
text = word_tokenize(alice)
text = nltk.pos_tag(hello)
# [('And', 'CC'), ('now', 'RB'), ('for', 'IN'), ('something', 'NN'),
# ('completely', 'RB'), ('different', 'JJ')]

In [73]:
pos_text = []
for tup in text:
    pos_word = tup[0] + tup[1]
    pos_text.append(pos_word)

In [74]:
Counter(pos_text)

Counter({'hurtJJ': 1,
         'hearthNN': 1,
         'showVBP': 2,
         'bottleVB': 2,
         'slipJJ': 1,
         'bankNN': 4,
         'sobJJ': 2,
         'patRB': 1,
         'dodoVBZ': 1,
         'watchNN': 12,
         'hopelessNN': 1,
         'absenceNN': 1,
         'ridgeVBP': 1,
         'surpriseNN': 4,
         'noDT': 21,
         'tremblingJJ': 1,
         'butterflyNN': 1,
         'loseVB': 2,
         'outIN': 1,
         'skyJJ': 3,
         'canaryJJ': 1,
         'occurJJR': 1,
         'meetVB': 1,
         'backRB': 2,
         'turtleNN': 44,
         'childhoodNN': 1,
         'crouchJJ': 1,
         'answerVBN': 1,
         'somewhereJJ': 1,
         'queerNN': 4,
         'stopVB': 3,
         'mushroomNN': 6,
         'thoroughlyRB': 2,
         'pronounceNN': 1,
         'denyJJ': 2,
         'cheshireJJ': 3,
         'childNNS': 1,
         'toTO': 4,
         'lengthNN': 1,
         'worthNN': 1,
         'leanJJ': 2,
         'showerNN': 1,
   

In [75]:
alice

'Alice was beginning to get very tired of sitting by her sister on the bank, and of having nothing to do: once or twice she had peeped into the book her sister was reading, but it had no pictures or conversations in it, \'and what is the use of a book,\' thought Alice \'without pictures or conversation?\' So she was considering in her own mind (as well as she could, for the hot day made her feel very sleepy and stupid), whether the pleasure of making a daisy-chain would be worth the trouble of getting up and picking the daisies, when suddenly a White Rabbit with pink eyes ran close by her. There was nothing so VERY remarkable in that; nor did Alice think it so VERY much out of the way to hear the Rabbit say to itself, \'Oh dear! Oh dear! I shall be late!\' (when she thought it over afterwards, it occurred to her that she ought to have wondered at this, but at the time it all seemed quite natural); but when the Rabbit actually TOOK A WATCH OUT OF ITS WAISTCOAT-POCKET, and looked at it, 

In [76]:
# Utility function to create a list of the 2000 most common words.
def bag_of_pos_words(text):
    
    # Filter out punctuation and stop words.
    allwords = [token.lemma_
                for token in text
                if not token.is_punct
                and not token.is_stop]
    
    allwords = nltk.pos_tag(allwords)
    
    pos_text = []
    for tup in allwords:
        pos_word = tup[0] + tup[1]
        pos_text.append(pos_word)
    # Return the most common words.
    return [item[0] for item in Counter(pos_text).most_common(1000)]
    
# Set up the bags.
alicewords2 = bag_of_pos_words(alice_doc)
persuasionwords2 = bag_of_pos_words(persuasion_doc)

# Combine bags to create a set of unique words.
common_words2 = set(alicewords2 + persuasionwords2)

In [77]:
common_words2

{'bottleVB',
 'objectNN',
 'surpriseNN',
 'showVBP',
 'sobJJ',
 'watchNN',
 'reasonNN',
 'acknowledgeVBP',
 'simpleJJ',
 'absenceNN',
 'noDT',
 'loseVB',
 'backRB',
 'turtleNN',
 'queerNN',
 'choiceNN',
 'considerableJJ',
 'stopVB',
 'mushroomNN',
 'thoroughlyRB',
 'denyJJ',
 'cheshireJJ',
 'toTO',
 'leanJJ',
 'stayVB',
 'pepperIN',
 'smileJJ',
 'commonJJ',
 'sightVBD',
 'needVBP',
 'growJJ',
 'serviceNN',
 'schoolNN',
 'musgroveIN',
 'closeRB',
 'mrsNN',
 'lizardNN',
 'aloudJJ',
 'friendVBP',
 'thatDT',
 'produceVBP',
 'louisaJJ',
 'monkfordNN',
 'minuteJJ',
 'knowledgeNN',
 'painfulJJ',
 'insteadRB',
 'catVB',
 'removeVB',
 'callNN',
 'breathNN',
 'hearNN',
 'fishJJ',
 'flyNN',
 'setVBN',
 'badJJ',
 'singVBG',
 'encourageNN',
 'earJJ',
 'probablyRB',
 'appearVBP',
 'letVB',
 'mortificationNN',
 'jurymanNN',
 'neckNN',
 'truthNN',
 'civilityNN',
 'neverRB',
 'difficultJJ',
 'mindNN',
 'holeNN',
 'concernNN',
 'consciousJJ',
 'majestyNNS',
 'improvementNN',
 'angryJJ',
 'attemptNN',
 '

In [78]:
# Creates a data frame with features for each word in our common word set.
# Each value is the count of the times the word appears in each sentence.
def bow_features2(sentences, common_words):
    
    # Scaffold the data frame and initialize counts to zero.
    df = pd.DataFrame(columns=common_words)
    df['text_sentence'] = sentences[0]
    df['text_source'] = sentences[1]
    df.loc[:, common_words] = 0
    
    # Process each row, counting the occurrence of words in each sentence.
    for i, sentence in enumerate(df['text_sentence']):
        
        # Convert the sentence to lemmas, then filter out punctuation,
        # stop words, and uncommon words.
        words = [token.lemma_
                 for token in sentence
                 if (
                     not token.is_punct
                     and not token.is_stop
                     and token.lemma_ in common_words
                 )]
        
        words = nltk.pos_tag(words)
    
        pos_text = []
        for tup in words:
            pos_word = tup[0] + tup[1]
            pos_text.append(pos_word)
        
        
        # Populate the row with word counts.
        for word in pos_text:
            df.loc[i, word] += 1
        
        # This counter is just to make sure the kernel didn't hang.
        if i % 500 == 0:
            print("Processing row {}".format(i))
            
    return df

# Create our data frame with features. This can take a while to run.

word_counts2 = bow_features2(sentences, common_words2)
word_counts2.head()

Processing row 0
Processing row 500
Processing row 1000
Processing row 1500
Processing row 2000
Processing row 2500
Processing row 3000
Processing row 3500
Processing row 4000
Processing row 4500
Processing row 5000


bottleVB objectNN surpriseNN showVBP sobJJ watchNN reasonNN acknowledgeVBP  \
0        0        0          0       0     0       0        0              0   
1        0        0          0       0     0       0        0              0   
2        0        0          0       0     0       0        0              0   
3        0        0          0       0     0       0        0              0   
4        0        0          0       0     0       0        0              0   

  simpleJJ absenceNN     ...     followVB illNN affectionNN delightedVBD  \
0        0         0     ...            0     0           0            0   
1        0         0     ...            0     0           0            0   
2        0         0     ...            0     0           0            0   
3        0         0     ...            0     0           0            0   
4        0         0     ...            0     0           0            0   

  resultNN perfectlyRB springNN subjectJJ  \
0        0           0        0         0   
1        0           0        0         0   
2        0           0        0         0   
3        0           0        0         0   
4        0           0        0         0   

                                       text_sentence text_source  
0  (Alice, was, beginning, to, get, very, tired, ...     Carroll  
1  (So, she, was, considering, in, her, own, mind...     Carroll  
2  (There, was, nothing, so, VERY, remarkable, in...     Carroll  
3                                      (Oh, dear, !)     Carroll  
4                         (I, shall, be, late, !, ')     Carroll  

[5 rows x 1589 columns]

In [134]:
word_counts2.head()

bottleVB objectNN surpriseNN showVBP sobJJ watchNN reasonNN acknowledgeVBP  \
0        0        0          0       0     0       0        0              0   
1        0        0          0       0     0       0        0              0   
2        0        0          0       0     0       0        0              0   
3        0        0          0       0     0       0        0              0   
4        0        0          0       0     0       0        0              0   

  simpleJJ absenceNN noDT loseVB backRB turtleNN queerNN choiceNN  \
0        0         0    0      0      0        0       0        0   
1        0         0    0      0      0        0       0        0   
2        0         0    0      0      0        0       0        0   
3        0         0    0      0      0        0       0        0   
4        0         0    0      0      0        0       0        0   

  considerableJJ stopVB mushroomNN thoroughlyRB denyJJ cheshireJJ toTO leanJJ  \
0              0      0          0            0      0          0    0      0   
1              0      0          0            0      0          0    0      0   
2              0      0          0            0      0          0    0      0   
3              0      0          0            0      0          0    0      0   
4              0      0          0            0      0          0    0      0   

  stayVB pepperIN smileJJ commonJJ sightVBD needVBP growJJ serviceNN schoolNN  \
0      0        0       0        0        0       0      0         0        0   
1      0        0       0        0        0       0      0         0        0   
2      0        0       0        0        0       0      0         0        0   
3      0        0       0        0        0       0      0         0        0   
4      0        0       0        0        0       0      0         0        0   

  musgroveIN closeRB mrsNN lizardNN aloudJJ friendVBP thatDT produceVBP  \
0          0       0     0        0       0         0      0          0   
1          0       0     0        0       0         0      0          0   
2          0       0     0        0       0         0      0          0   
3          0       0     0        0       0         0      0          0   
4          0       0     0        0       0         0      0          0   

  louisaJJ monkfordNN minuteJJ knowledgeNN painfulJJ insteadRB catVB removeVB  \
0        0          0        0           0         0         0     0        0   
1        0          0        0           0         0         0     0        0   
2        0          0        0           0         0         0     0        0   
3        0          0        0           0         0         0     0        0   
4        0          0        0           0         0         0     0        0   

  callNN breathNN hearNN fishJJ flyNN setVBN badJJ singVBG encourageNN earJJ  \
0      0        0      0      0     0      0     0       0           0     0   
1      0        0      0      0     0      0     0       0           0     0   
2      0        0      0      0     0      0     0       0           0     0   
3      0        0      0      0     0      0     0       0           0     0   
4      0        0      0      0     0      0     0       0           0     0   

  probablyRB appearVBP letVB mortificationNN jurymanNN neckNN truthNN  \
0          0         0     0               0         0      0       0   
1          0         0     0               0         0      0       0   
2          0         0     0               0         0      0       0   
3          0         0     0               0         0      0       0   
4          0         0     0               0         0      0       0   

  civilityNN neverRB difficultJJ mindNN holeNN concernNN consciousJJ  \
0          0       0           0      0      0         0           0   
1          0       0           0      0      0         0           0   
2          0       0           0      0      0         0  

In [190]:
list(word_counts2.columns)

['bottleVB',
 'objectNN',
 'surpriseNN',
 'showVBP',
 'sobJJ',
 'watchNN',
 'reasonNN',
 'acknowledgeVBP',
 'simpleJJ',
 'absenceNN',
 'noDT',
 'loseVB',
 'backRB',
 'turtleNN',
 'queerNN',
 'choiceNN',
 'considerableJJ',
 'stopVB',
 'mushroomNN',
 'thoroughlyRB',
 'denyJJ',
 'cheshireJJ',
 'toTO',
 'leanJJ',
 'stayVB',
 'pepperIN',
 'smileJJ',
 'commonJJ',
 'sightVBD',
 'needVBP',
 'growJJ',
 'serviceNN',
 'schoolNN',
 'musgroveIN',
 'closeRB',
 'mrsNN',
 'lizardNN',
 'aloudJJ',
 'friendVBP',
 'thatDT',
 'produceVBP',
 'louisaJJ',
 'monkfordNN',
 'minuteJJ',
 'knowledgeNN',
 'painfulJJ',
 'insteadRB',
 'catVB',
 'removeVB',
 'callNN',
 'breathNN',
 'hearNN',
 'fishJJ',
 'flyNN',
 'setVBN',
 'badJJ',
 'singVBG',
 'encourageNN',
 'earJJ',
 'probablyRB',
 'appearVBP',
 'letVB',
 'mortificationNN',
 'jurymanNN',
 'neckNN',
 'truthNN',
 'civilityNN',
 'neverRB',
 'difficultJJ',
 'mindNN',
 'holeNN',
 'concernNN',
 'consciousJJ',
 'majestyNNS',
 'improvementNN',
 'angryJJ',
 'attemptNN',
 '

In [194]:
word_counts2[word_counts2[list(word_counts2.columns)] > 0]

bottleVB objectNN surpriseNN showVBP sobJJ watchNN reasonNN  \
0         NaN      NaN        NaN     NaN   NaN     NaN      NaN   
1         NaN      NaN        NaN     NaN   NaN     NaN      NaN   
2         NaN      NaN        NaN     NaN   NaN     NaN      NaN   
3         NaN      NaN        NaN     NaN   NaN     NaN      NaN   
4         NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5         NaN      NaN        NaN     NaN   NaN     NaN      NaN   
6         NaN      NaN        NaN     NaN   NaN     NaN      NaN   
7         NaN      NaN        NaN     NaN   NaN     NaN      NaN   
8         NaN      NaN        NaN     NaN   NaN     NaN      NaN   
9         NaN      NaN        NaN     NaN   NaN     NaN      NaN   
10        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
11        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
12        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
13        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
14        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
15        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
16        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
17        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
18        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
19        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
20        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
21        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
22        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
23        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
24        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
25        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
26        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
27        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
28        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
29        NaN      NaN        NaN     NaN   NaN     NaN      NaN   
...       ...      ...        ...     ...   ...     ...      ...   
5288      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5289      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5290      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5291      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5292      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5293      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5294      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5295      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5296      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5297      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5298      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5299      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5300      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5301      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5302      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5303      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5304      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5305      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5306      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5307      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5308      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5309      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5310      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5311      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5312      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5313      NaN      NaN        NaN     NaN   NaN     NaN      NaN   
5314      NaN      NaN        NaN     NaN   NaN     NaN      

In [79]:
word_counts2 = word_counts2.drop(['text_sentence', 'text_source'],1)

word_counts3 = word_counts.join(word_counts2)

In [80]:
Y3 = word_counts3['text_source']
X3 = np.array(word_counts3.drop(['text_sentence','text_source'], 1))

X3_train, X3_test, y3_train, y3_test = train_test_split(X3, 
                                                    Y3,
                                                    test_size=0.2,
                                                    random_state=0)

lr5 = LogisticRegression()
train = lr5.fit(X3_train, y3_train)
print(X3_train.shape, y3_train.shape)
print('Training set score:', lr5.score(X3_train, y3_train))
print('\nTest set score:', lr5.score(X3_test, y3_test))

(4254, 4652) (4254,)
Training set score: 0.960272684532

Test set score: 0.923872180451


In [100]:
# Utility function to create a list of the 2000 most common words.
def bag_of_pos(text):
    
    # View the part of speech for some tokens in our sentence.
    parts_of_speech = []
    for token in text:
        parts_of_speech.append(token.pos_)
    # Return list of all parts of speech
    return Counter(parts_of_speech).keys() 
    
# Set up the bags.
alicepos = bag_of_pos(alice_doc)
persuasionpos = bag_of_pos(persuasion_doc)

# Combine bags to create a set of unique words.
common_pos = list(set(list(alicepos) + list(persuasionpos)))

In [101]:
common_pos

['ADV',
 'PRON',
 'PART',
 'VERB',
 'INTJ',
 'DET',
 'ADJ',
 'NUM',
 'X',
 'PROPN',
 'ADP',
 'CCONJ',
 'NOUN',
 'PUNCT']

In [103]:
# Creates a data frame with features for each word in our common word set.
# Each value is the count of the times the word appears in each sentence.
def pos_features(sentences, common_pos):
    
    # Scaffold the data frame and initialize counts to zero.
    df = pd.DataFrame(columns=common_pos)
    df['text_sentence'] = sentences[0]
    df['text_source'] = sentences[1]
    df.loc[:, common_pos] = 0
    
    # Process each row, counting the occurrence of words in each sentence.
    for i, sentence in enumerate(df['text_sentence']):
        
        # View the part of speech for some tokens in our sentence.
        parts_of_speech = []
        for token in sentence:
            parts_of_speech.append(token.pos_)
        # Return list of all parts of speech
        
        pos_list = list(Counter(parts_of_speech).keys())
        
        # Populate the row with word counts.
        for pos in pos_list:
            df.loc[i, pos] += 1
        
        # This counter is just to make sure the kernel didn't hang.
        if i % 500 == 0:
            print("Processing row {}".format(i))
            
    return df

# Create our data frame with features. This can take a while to run.
pos_counts = pos_features(sentences, common_pos)
pos_counts = pos_counts.drop(['text_sentence','text_source'], 1)
pos_counts.head()

Processing row 0
Processing row 500
Processing row 1000
Processing row 1500
Processing row 2000
Processing row 2500
Processing row 3000
Processing row 3500
Processing row 4000
Processing row 4500
Processing row 5000


ADV PRON PART VERB INTJ DET ADJ NUM  X PROPN ADP CCONJ NOUN PUNCT
0   1    1    1    1    0   1   1   0  0     1   1     1    1     1
1   1    1    1    1    0   1   1   0  0     1   1     1    1     1
2   1    1    1    1    1   1   1   0  0     1   1     1    1     1
3   0    0    0    0    1   0   0   0  0     0   0     0    0     1
4   0    1    0    1    0   0   1   0  0     0   0     0    0     1

In [159]:
count_sent_pos = word_sent_counts.join(pos_counts)

In [160]:
count_sent_pos.head()

keep behaviour style bustle vision degrading earnestly fortune toffee  \
0    0         0     0      0      0         0         0       0      0   
1    0         0     0      0      0         0         0       0      0   
2    0         0     0      0      0         0         0       0      0   
3    0         0     0      0      0         0         0       0      0   
4    0         0     0      0      0         0         0       0      0   

  calculate dowager previous revert composedly saucer cook smiths twelve  \
0         0       0        0      0          0      0    0      0      0   
1         0       0        0      0          0      0    0      0      0   
2         0       0        0      0          0      0    0      0      0   
3         0       0        0      0          0      0    0      0      0   
4         0       0        0      0          0      0    0      0      0   

  caper principal egg care scarcely person timidly fresh remarkably less  \
0     0         0   0    0        0      0       0     0          0    0   
1     0         0   0    0        0      0       0     0          0    0   
2     0         0   0    0        0      0       0     0          0    0   
3     0         0   0    0        0      0       0     0          0    0   
4     0         0   0    0        0      0       0     0          0    0   

  publication tolerable monday counsel powerful good have ship nest down  \
0           0         0      0       0        0    0    1    0    0    0   
1           0         0      0       0        0    0    0    0    0    0   
2           0         0      0       0        0    0    0    0    0    0   
3           0         0      0       0        0    0    0    0    0    0   
4           0         0      0       0        0    0    0    0    0    0   

  conquest caution charles offence connexion busy condition free destroy  \
0        0       0       0       0         0    0         0    0       0   
1        0       0       0       0         0    0         0    0       0   
2        0       0       0       0         0    0         0    0       0   
3        0       0       0       0         0    0         0    0       0   
4        0       0       0       0         0    0         0    0       0   

  aside lower uncommon pennyworth bottle death hopeless art understand  \
0     0     0        0          0      0     0        0   0          0   
1     0     0        0          0      0     0        0   0          0   
2     0     0        0          0      0     0        0   0          0   
3     0     0        0          0      0     0        0   0          0   
4     0     0        0          0      0     0        0   0          0   

  purchase till tenderness severity courteous pour cherry fair joy john alarm  \
0        0    0          0        0         0    0      0    0   0    0     0   
1        0    0          0        0         0    0      0    0   0    0     0   
2        0    0          0        0         0    0      0    0   0    0     0   
3        0    0          0        0         0    0      0    0   0    0     0   
4        0    0          0        0         0    0      0    0   0    0     0   

  comfortable alarming howl lay private marlborough station acknowledge dinn  \
0           0        0    0   0       0           0       0           0    0   
1           0        0    0   0       0           0       0           0    0   
2           0        0    0   0       0           0       0           0    0   
3           0        0    0   0       0           0       0           0    0   
4           0        0    0   0       0           0       0           0    0   

  sulkily rule rudeness sight reflect tease scale ten mabel artificial  \
0       0    0        0     0       0     0     0   0     0          0   
1       0    0        0     0       0     0     0   0     0          0   
2       0    0        0     0       0     0     0   0     0          0   
3       0    0

### Adding the POS made it slightly worse, both for logistic regression and support vector machines... :-/

In [161]:
Y = count_sent_pos['text_source']
X = np.array(count_sent_pos.drop(['text_sentence','text_source'], 1))

X_train, X_test, y_train, y_test = train_test_split(X, 
                                                    Y,
                                                    test_size=0.2,
                                                    random_state=0)

lr6 = LogisticRegression()
train = lr6.fit(X_train, y_train)


print(X_train.shape, y_train.shape)
print('Training set score with all features:', lr5.score(X_train, y_train))
print('\nTest set score with all features:', lr5.score(X_test, y_test))

print('\nTraining set score with sentence features:', log_reg_train_score2)
print('\nTest set score with sentence features:', log_reg_text_score2)

print('\nOriginal Log Regression Train Score: ', log_reg_train_score1)
print('\nOriginal Log Regression Test Score: ', log_reg_test_score1)

(4254, 3079) (4254,)
Training set score with all features: 0.959802538787

Test set score with all features: 0.927631578947

Training set score with sentence features: 0.960272684532

Test set score with sentence features: 0.923872180451

Original Log Regression Train Score:  0.956511518571

Original Log Regression Test Score:  0.926691729323


In [185]:
Y = word_counts['text_source']
X = np.array(word_counts.drop(['text_sentence','text_source'], 1))

print(cross_val_score(lr6, X, Y, cv = 5))

[ 0.89003759  0.86842105  0.91917293  0.90883459  0.89642185]


In [186]:
np.mean([0.89003759, 0.86842105, 0.91917293, 0.90883459, 0.89642185])

0.89657760200000003

In [187]:
Y = word_sent_counts['text_source']
X = np.array(word_sent_counts.drop(['text_sentence','text_source'], 1))

print(cross_val_score(lr6, X, Y, cv = 5))

[ 0.8825188   0.87593985  0.92669173  0.91071429  0.89642185]


In [188]:
np.mean([0.8825188, 0.87593985, 0.92669173, 0.91071429, 0.89642185])

0.89845730400000012

In [183]:
Y = count_sent_pos['text_source']
X = np.array(count_sent_pos.drop(['text_sentence','text_source'], 1))

print(cross_val_score(lr6, X, Y, cv = 5))

[ 0.8787594   0.875       0.92105263  0.91259398  0.89830508]


In [184]:
np.mean([0.8787594, 0.875, 0.92105263, 0.91259398, 0.89830508])

0.89714221799999994

In [175]:
Y = count_sent_pos['text_source']
X = np.array(count_sent_pos.drop(['text_sentence','text_source'], 1))

X_train, X_test, y_train, y_test = train_test_split(X, 
                                                    Y,
                                                    test_size=0.2,
                                                    random_state=0)



svm3 = SVC(kernel = 'linear')
svm3.fit(X_train, y_train)

svm_train_score3 = svm3.score(X_train, y_train)
svm_test_score3 = svm3.score(X_test, y_test)

print('Training set score with sentance and pov features:', svm_train_score3)
print('\nTest set score with sentance and pov features:', svm_test_score3)

print('\nTraining set score with sentance features:', svm_train_score2)
print('\nTest set score with sentance features:', svm_test_score2)

print('\nTraining set score original features:', svm_train_score1)
print('\nTest set score original features:', svm_test_score1)

Training set score with sentance and pov features: 0.974141984015

Test set score with sentance and pov features: 0.924812030075

Training set score with sentance features: 0.974847202633

Test set score with sentance features: 0.925751879699

Training set score original features: 0.967795016455

Test set score original features: 0.913533834586


In [178]:
Y = word_counts['text_source']
X = np.array(word_counts.drop(['text_sentence','text_source'], 1))

print(cross_val_score(svm, X, Y, cv = 5))

[ 0.8787594   0.85996241  0.92199248  0.89473684  0.87947269]


In [180]:
np.mean([0.8787594, 0.85996241, 0.92199248, 0.89473684, 0.87947269])

0.88698476399999993

In [177]:
Y = word_sent_counts['text_source']
X = np.array(word_sent_counts.drop(['text_sentence','text_source'], 1))

print(cross_val_score(svm2, X, Y, cv = 5))

[ 0.87781955  0.86654135  0.91917293  0.90037594  0.88512241]


In [181]:
np.mean([0.87781955, 0.86654135, 0.91917293, 0.90037594, 0.88512241])

0.88980643599999998

In [176]:
Y = count_sent_pos['text_source']
X = np.array(count_sent_pos.drop(['text_sentence','text_source'], 1))

print(cross_val_score(svm3, X, Y, cv = 5))  


[ 0.8843985   0.8731203   0.92387218  0.89285714  0.89077213]


In [182]:
np.mean([0.8843985,0.8731203, 0.92387218, 0.89285714, 0.89077213])

0.89300405000000005

In [128]:
pd.options.display.max_columns = None

In [129]:
count_sent_pos.head()

keep behaviour style bustle vision degrading earnestly fortune toffee  \
0    0         0     0      0      0         0         0       0      0   
1    0         0     0      0      0         0         0       0      0   
2    0         0     0      0      0         0         0       0      0   
3    0         0     0      0      0         0         0       0      0   
4    0         0     0      0      0         0         0       0      0   

  calculate dowager previous revert composedly saucer cook smiths twelve  \
0         0       0        0      0          0      0    0      0      0   
1         0       0        0      0          0      0    0      0      0   
2         0       0        0      0          0      0    0      0      0   
3         0       0        0      0          0      0    0      0      0   
4         0       0        0      0          0      0    0      0      0   

  caper principal egg care scarcely person timidly fresh remarkably less  \
0     0         0   0    0        0      0       0     0          0    0   
1     0         0   0    0        0      0       0     0          0    0   
2     0         0   0    0        0      0       0     0          0    0   
3     0         0   0    0        0      0       0     0          0    0   
4     0         0   0    0        0      0       0     0          0    0   

  publication tolerable monday counsel powerful good have ship nest down  \
0           0         0      0       0        0    0    1    0    0    0   
1           0         0      0       0        0    0    0    0    0    0   
2           0         0      0       0        0    0    0    0    0    0   
3           0         0      0       0        0    0    0    0    0    0   
4           0         0      0       0        0    0    0    0    0    0   

  conquest caution charles offence connexion busy condition free destroy  \
0        0       0       0       0         0    0         0    0       0   
1        0       0       0       0         0    0         0    0       0   
2        0       0       0       0         0    0         0    0       0   
3        0       0       0       0         0    0         0    0       0   
4        0       0       0       0         0    0         0    0       0   

  aside lower uncommon pennyworth bottle death hopeless art understand  \
0     0     0        0          0      0     0        0   0          0   
1     0     0        0          0      0     0        0   0          0   
2     0     0        0          0      0     0        0   0          0   
3     0     0        0          0      0     0        0   0          0   
4     0     0        0          0      0     0        0   0          0   

  purchase till tenderness severity courteous pour cherry fair joy john alarm  \
0        0    0          0        0         0    0      0    0   0    0     0   
1        0    0          0        0         0    0      0    0   0    0     0   
2        0    0          0        0         0    0      0    0   0    0     0   
3        0    0          0        0         0    0      0    0   0    0     0   
4        0    0          0        0         0    0      0    0   0    0     0   

  comfortable alarming howl lay private marlborough station acknowledge dinn  \
0           0        0    0   0       0           0       0           0    0   
1           0        0    0   0       0           0       0           0    0   
2           0        0    0   0       0           0       0           0    0   
3           0        0    0   0       0           0       0           0    0   
4           0        0    0   0       0           0       0           0    0   

  sulkily rule rudeness sight reflect tease scale ten mabel artificial  \
0       0    0        0     0       0     0     0   0     0          0   
1       0    0        0     0       0     0     0   0     0          0   
2       0    0        0     0       0     0     0   0     0          0   
3       0    0

### I realize that the data frame I got was all zeroes for the POS... Let's see if i can figure out how to fix it!!!

In [ ]:
# # Creates a data frame with features for each word in our common word set.
# # Each value is the count of the times the word appears in each sentence.
# def pos_features3(sentences, common_words):
    
#     # Scaffold the data frame and initialize counts to zero.
#     df = pd.DataFrame(columns=common_words)
#     df['text_sentence'] = sentences[0]
#     df['text_source'] = sentences[1]
#     df.loc[:, common_words] = 0
    
#     # Process each row, counting the occurrence of words in each sentence.
#     for i, sentence in enumerate(df['text_sentence']):
        
#         # Convert the sentence to lemmas, then filter out punctuation,
#         # stop words, and uncommon words.
#         words = [token.lemma_
#                  for token in sentence
#                  if (
#                      not token.is_punct
#                      and not token.is_stop
#                      and token.lemma_ in common_words
#                  )]
        
#         words = nltk.pos_tag(words)
    
#         pos_text = []
#         for tup in words:
#             pos_word = tup[0] + tup[1]
#             pos_text.append(pos_word)
        
        
#         # Populate the row with word counts.
#         for word in pos_text:
#             df.loc[i, word] += 1
        
#         # This counter is just to make sure the kernel didn't hang.
#         if i % 500 == 0:
#             print("Processing row {}".format(i))
            
#     return df

# # Create our data frame with features. This can take a while to run.

# pos_counts3 = pos_features3(sentences, common_words2)
# pos_counts3.head()